In [1]:
'''
M1. Actividad
Vacuum cleaner

Authors:
Luis Alberto Alcántara Cabrales A01634185
Alexa Serrano Negrete A01654063
Renet de Jesús Pérez Gómez A01640555
Vicente Javier Viera Guízar A01639784

Date:
11/14/2022
'''

# Model design
import agentpy as ap
import random

# Visualization
import matplotlib.pyplot as plt
import seaborn as sns
import IPython

#Global variable
MOVES = [(0,1), (0,-1), (1,0), (-1,0), (1,1), (1,-1), (-1,1), (-1,-1)]

In [2]:
class MyModel(ap.Model):
    def setup(self):
        
        #Create agents
        nGarbage = int(self.p.dirtDensity * (self.p.M * self.p.N))
        self.garbage = ap.AgentList(self, nGarbage) 
        self.robot = ap.AgentList(self, self.p.agents)
        
        
        #Create grid model
        self.area = ap.Grid(self, [self.p.M, self.p.N])
        
        #Add the agents to the enviroment
        self.area.add_agents(self.garbage, random=True)
        robotPosition = [(1,1) for _ in range (len(self.robot))]
        self.area.add_agents(self.robot, positions = robotPosition)
        
        #Initiate dynamic variable for agents
        self.robot.condition = 0
        self.garbage.condition = 1
        
        #Initiate dynamic variable for robot movement
        self.cleaning = 0
        self.movements = 0
        
    def step(self):
        
        # Change pending garbage condition
        garbageRemoved = self.garbage.select(self.garbage.condition == 0)
        garbageRemoved.condition = 2
        
        for robot in self.robot:
            #Saves robot position
            robotPosition = self.area.positions[robot]
            
            #Saves remaining garbage to clean
            remainingGarbage = self.garbage.select(self.garbage.condition == 1)
            
            #Checks if the cell is dirty
            for garbage in remainingGarbage:
                if self.area.positions[garbage] == robotPosition:
                    garbage.condition = 0
                    self.cleaning = 1
                 
            #Checks if the robot finds a cell to clean
            #If the robot is not cleaning:
            if self.cleaning == 0:
                #Generates a random position
                randomMove = random.choice(MOVES)
                [x, y] = robotPosition
                [x, y] = [x + randomMove[0], y + randomMove[1]]
                
                #Checks that the new position is within the grid
                if x <= self.p.M and y <= self.p.N and x >= 0 and y >= 0:
                    self.area.move_by(robot, randomMove)     
                    self.movements += 1
            #If the robot is cleaning:
            elif self.cleaning == 1:
                #If the robot is cleaning
                self.cleaning = 0
        
        #The experiment stops until there's no trash
        if len(self.garbage.select(self.garbage.condition == 1)) == 0:
            self.stop()
        
    def end(self):
         # Document a measure at the end of the simulation
        cleanedTrash = len(self.garbage.select(self.garbage.condition == 2))
        self.report('Percentage of cleaned trash', (round(cleanedTrash / len(self.garbage)) * 100, 2))

In [3]:
#Parameters
parameters = {
    'M': 30,
    'N': 20,
    'agents': 100,
    'dirtDensity': 0.3,
    'steps': 250
}

In [4]:
def animation_plot(model, ax):
    attr_grid = model.area.attr_grid('condition')
    color_dict = {0:'#00611a', 1:'#9e9e9e', 2:'#e5e5e5', None:'#d5e5d5'}
    ap.gridplot(attr_grid, ax=ax, color_dict=color_dict, convert=True)
    cleanedTrash = len(model.garbage.select(model.garbage.condition == 2))
    ax.set_title(f"Simulation of a vacuum cleaner\n"
                 f"Time-step: {model.t}, Trash left: "
                 f"{len(model.garbage.select(model.garbage.condition == 1))}, "
                 f"Movements: {model.movements}\n"
                 f"Percentage of cleaned trash: {round((cleanedTrash / len(model.garbage)) * 100, 2)}%")
    
fig, ax = plt.subplots()
model = MyModel(parameters)
animation = ap.animate(model, fig, ax, animation_plot)

IPython.display.HTML(animation.to_jshtml(fps=1))